In [157]:
import numpy as np
from sklearn.metrics.cluster._supervised import contingency_matrix, check_clusterings
def pair_confusion_matrix(labels_true, labels_pred):
    """Pair confusion matrix arising from two clusterings.
    The pair confusion matrix :math:`C` computes a 2 by 2 similarity matrix
    between two clusterings by considering all pairs of samples and counting
    pairs that are assigned into the same or into different clusters under
    the true and predicted clusterings.
    Considering a pair of samples that is clustered together a positive pair,
    then as in binary classification the count of true negatives is
    :math:`C_{00}`, false negatives is :math:`C_{10}`, true positives is
    :math:`C_{11}` and false positives is :math:`C_{01}`.
    Read more in the :ref:`User Guide <pair_confusion_matrix>`.
    Parameters
    ----------
    labels_true : array-like of shape (n_samples,), dtype=integral
        Ground truth class labels to be used as a reference.
    labels_pred : array-like of shape (n_samples,), dtype=integral
        Cluster labels to evaluate.
    Returns
    -------
    C : ndarray of shape (2, 2), dtype=np.int64
        The contingency matrix.
    See Also
    --------
    rand_score: Rand Score
    adjusted_rand_score: Adjusted Rand Score
    adjusted_mutual_info_score: Adjusted Mutual Information
    Examples
    --------
    Perfectly matching labelings have all non-zero entries on the
    diagonal regardless of actual label values:
      >>> from sklearn.metrics.cluster import pair_confusion_matrix
      >>> pair_confusion_matrix([0, 0, 1, 1], [1, 1, 0, 0])
      array([[8, 0],
             [0, 4]]...
    Labelings that assign all classes members to the same clusters
    are complete but may be not always pure, hence penalized, and
    have some off-diagonal non-zero entries:
      >>> pair_confusion_matrix([0, 0, 1, 2], [0, 0, 1, 1])
      array([[8, 2],
             [0, 2]]...
    Note that the matrix is not symmetric.
    References
    ----------
    .. L. Hubert and P. Arabie, Comparing Partitions, Journal of
      Classification 1985
      https://link.springer.com/article/10.1007%2FBF01908075
    """
    labels_true, labels_pred = check_clusterings(labels_true, labels_pred)
    n_samples = np.int64(labels_true.shape[0])

    # Computation using the contingency data
    contingency = contingency_matrix(
        labels_true, labels_pred, sparse=True
        )#, dtype=np.int64)
    n_c = np.ravel(contingency.sum(axis=1))
    n_k = np.ravel(contingency.sum(axis=0))
    sum_squares = (contingency.data ** 2).sum()
    C = np.empty((2, 2), dtype=np.int64)
    C[1, 1] = sum_squares - n_samples
    C[0, 1] = contingency.dot(n_k).sum() - sum_squares
    C[1, 0] = contingency.transpose().dot(n_c).sum() - sum_squares
    C[0, 0] = n_samples ** 2 - C[0, 1] - C[1, 0] - sum_squares
    return C

In [158]:
import pandas as pd
akshit_df = './mlchallenge_set_2021.tsv'
akshit_valid = './mlchallenge_set_validation.tsv'
sam_df = 'C:/Users/sjmal/OneDrive/Desktop/ML/2021/mlchallenge_set_2021_edited.txt'
sam_valid = 'C:/Users/sjmal/OneDrive/Desktop/ML/2021/mlchallenge_set_validation.tsv'
sa_df = '/Users/shivankagrawal/Documents/ebay/mlchallenge_set_2021.tsv'
sa_valid = '/Users/shivankagrawal/Documents/ebay/mlchallenge_set_validation.tsv'
SA_valid=pd.read_table(akshit_valid,header=None)
SA_df=pd.read_table(akshit_df,header=None)
df=SA_df
valid=SA_valid
#df = pd.read_table(sam_df)
#valid = pd.read_table(sam_valid,sep='\t')
df.columns=['category','primary_image_url','All Links','Tags','index']
valid.columns=['ID', 'Group']

In [160]:
"""
Import test output file as dataframe and set the index.
"""
output = './akshit.tsv'
predictions = pd.read_table(output,header=None)
predictions.columns = ['ID', 'Group']
predictions.set_index('ID', inplace=True)
valid.set_index('ID', inplace=True)

KeyError: "None of ['ID'] are in the columns"

In [162]:
print(predictions)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [163]:
"""
Compute confusion matrix for validation data. Use valid dataframe to extract values from a tsv output file.
"""
preds = []
actuals = []
for index, row in valid.iterrows():
    preds.append(predictions.loc[index]['Group'])
    actuals.append(row['Group'])
# print(preds[100:200])
# print(actuals[100:200])
def evaluate(actuals, preds):
    C = pair_confusion_matrix(actuals, preds)
    precision = C[1][1] / (C[1][1] + C[0][1]) # (true positives) / (true positives + false positives)
    recall = C[1][1] / (C[1][1] + C[1][0]) # (true positives) / (true positives + false negatives)
    print(f'Confusion Matrix:\n{C}')
    print(f'precision: {precision}')
    print(f'recall: {recall}')
    print(f'f1 score: {2 * precision * recall / (precision + recall)}')

evaluate(actuals, preds)

Confusion Matrix:
[[154807560      2892]
 [     3974      1380]]
precision: 0.32303370786516855
recall: 0.2577512140455734
f1 score: 0.2867234573031373


In [164]:
print(df.head())
print(valid.head())

   category  \
0  2          
1  2          
2  2          
3  2          
4  2          

                                                                       primary_image_url  \
0  https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/iYYAAOxydgZTJwYc/$_1.JPG?set_id=880000500F    
1  https://i.ebayimg.com/00/s/MTA1OFgxMTM0/z/KPIAAOSw4A5YoCoa/$_1.JPG?set_id=880000500F    
2  https://i.ebayimg.com/00/s/MTIwMFgxNjAw/z/flIAAOSwxH1UCdW5/$_1.JPG?set_id=880000500F    
3  http://i.ebayimg.com/00/s/ODAwWDEwNjc=/z/XHcAAOSwY45UUagU/$_1.JPG?set_id=880000500F     
4  https://i.ebayimg.com/00/s/MTA2N1gxNjAw/z/scsAAOSwj0NUlk96/$_12.JPG?set_id=880000500F   

                                                                                                                                                                                                                                                                                                                                                                    

In [7]:
#split links into list (for now only does first 100)
i = 0
for link in df['All Links'][0:100]:
    df['All Links'][i] = link.split(';')
    i+=1
print(df['All Links'][0:100])

<ipython-input-7-5e0f35be6386>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['All Links'][i] = link.split(';')


0     [https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/iYY...
1     [https://i.ebayimg.com/00/s/MTA1OFgxMTM0/z/KPI...
2     [https://i.ebayimg.com/00/s/MTIwMFgxNjAw/z/flI...
3     [http://i.ebayimg.com/00/s/ODAwWDEwNjc=/z/XHcA...
4     [https://i.ebayimg.com/00/s/MTA2N1gxNjAw/z/scs...
                            ...                        
95    [https://i.ebayimg.com/00/s/MTU5OVgxNTgx/z/vMA...
96    [https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/GoA...
97    [https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/Hm0...
98    [https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/VhA...
99    [https://i.ebayimg.com/00/s/MTYwMFgxNjAw/z/n4o...
Name: All Links, Length: 100, dtype: object


In [165]:
"""
Frequency counting of the tags in a particular category.
"""
import re
from collections import Counter
# for category in range(1, 6):
df = SA_df
df = df.loc[df['category'] == 5]
freq=Counter()
attribute=[['']]*len(df)
print('allocated array')
trialrange=len(df)
for x in range(0, trialrange, 5):#range(int(len(df)/10)):#len(df)
    attribute[x]=df.iloc[x,3].lower()
    attribute[x] = attribute[x][1:-1] # remove starting and ending parentheses
    attribute[x] = re.split(r',(?![^(]*\))', attribute[x]) # ignore commas that are inside parentheses
    attribute[x] = [a.split(':') for a in attribute[x]]
    freq+=Counter([i[0] for i in attribute[x]])
    tempdict={}
#     print(df.iloc[x,3])
    #print(attribute[x])
#     print(attribute)
    for i in attribute[x]:
        try:
            tempdict[i[0]]=float(i[1])
        except:
            try:
                tempdict[i[0]]=i[1]
            except:
                pass
    attribute[x]=tempdict
#     print(attribute[x])
df = SA_df
print("am out of loop")

allocated array
am out of loop


In [130]:
d = dict((k, v) for k, v in freq.items() if v > 20)
array = list(sorted(d, key=lambda k: d[k],reverse=True))[:10]
d= {k: v for k, v in sorted(d.items(), key=lambda item: item[1],reverse=True)}
print(d)
print(array)
import matplotlib.pyplot as plt
#import matplotlib.pyplot as plt
plt.bar(d.keys(),d.values())
plt.show()

{'brand': 30516, 'mpn': 26220, 'model': 14884, 'type': 13136, 'upc': 10914, 'ean': 7992, 'cord type': 7680, 'bagged/bagless': 6668, 'color': 6616, 'filters': 5183, 'features': 5057, 'manufacturer': 4469, 'isbn': 4066, 'country/region of manufacture': 3040, 'custom bundle': 2881, 'modified item': 2506, 'item weight': 2477, 'shipping weight': 2407, 'power': 2306, 'product dimensions': 2061, 'item model number': 1769, '': 1648, 'voltage': 1459, 'productgroup': 1260, 'non-domestic product': 1208, 'binding': 1151, 'included accessories': 1136, 'label': 1107, 'publisher': 1069, 'bag/bagless': 1042, 'item_length': 907, 'shipping': 887, 'manufacturer part number': 865, 'item_width': 853, 'edge cleaning': 811, 'partnumber': 809, 'size': 802, 'batteries': 796, 'weight': 782, 'category': 760, 'filter type': 758, 'style': 747, 'tax': 716, 'color family': 698, 'bundle listing': 681, 'amperage (amps)': 649, 'numberofitems': 617, 'cord length (ft.)': 591, 'handle controls': 589, 'carpet cleaning': 54

In [166]:
df = SA_df

In [180]:
import re
validation_rows = df.loc[df['index'].isin(valid.index)]
validation_rows = validation_rows.loc[validation_rows['category'] == 1]
keep_tags = ['brand', 'size type', "bottoms size (women's)", 'material', 'inseam', 'color', 'rise', 'style', 'silhouette', 'country/region of manufacture']
# df = category5
def register_attributes(attribute, all_attributes):
    attribute = attribute[1:-1].lower() # attribute = re.sub(r'[()]','', attribute)
    attribute = re.split(r',(?![^(]*\))', attribute)
    attribute = [a.split(':') for a in attribute]
    for i, a in enumerate(attribute):
        attribute[i] = [s.strip() for s in a]
        if attribute[i][0] in keep_tags:
            all_attributes.add(attribute[i][0])
    #print(f'atttribute is: {attribute}')
    mapping = {}
    #for i in range(len(attribute) - 1):
    #    if i == len(attribute) - 2:
    #        mapping[attribute[i][-1]] = attribute[i + 1][:]
    #    else:
    #        mapping[attribute[i][-1]] = attribute[i + 1][:-1]
    return(attribute)

def map_attributes(attribute, num_attributes, index_to_attr):
    attribute = attribute[1:-1].lower() # attribute = re.sub(r'[()]','', attribute)
    attribute = re.split(r',(?![^(]*\))', attribute)
    attribute = [a.split(':') for a in attribute]
    all_attributes_for_row = [None] * num_attributes
    for i, a in enumerate(attribute):
        attribute[i] = [s.strip() for s in a]
        #print(f'index: {attr_to_index[attribute[i][0]]}')
        if len(attribute[i]) > 1 and attribute[i][0] in keep_tags:
            all_attributes_for_row[attr_to_index[attribute[i][0]]] = attribute[i][1]
    mapping = {}
    #for i in range(len(attribute) - 1):
    #    if i == len(attribute) - 2:
    #        mapping[attribute[i][-1]] = attribute[i + 1][:]
    #    else:
    #        mapping[attribute[i][-1]] = attribute[i + 1][:-1]
    return all_attributes_for_row
m = 50000
all_attributes = set()
all_maps = []
for index,row in validation_rows[0:].iterrows():
    register_attributes(row['Tags'], all_attributes)

all_attributes = list(all_attributes)
attr_to_index = {all_attributes[i]: i for i in range(len(all_attributes))}
#print(attr_to_index)
#print(f'numAttributes: {len(all_attributes)}')

for index,row in validation_rows[0:].iterrows():
    all_maps.append(map_attributes(row['Tags'], len(all_attributes), attr_to_index))
possible_vals = set()
from collections import Counter
c = Counter()
for v in all_maps:
    print(v)
    possible_vals.update(v)
    c.update(v)
print(len(possible_vals))
print(c)

['old navy', None, None, '14', 'slim', '28', None, 'juniors', 'mid-rise', 'denim']
['american eagle outfitters', 'blue', None, '6', 'flare', '29', 'china', 'regular', 'low', 'cotton blend']
['paige', 'white', None, '29', 'wide leg', '34"', None, 'regular', 'mid-rise', 'cotton and spandex']
['old navy', 'blue', 'bootcut', '10', None, '32', None, 'regular', 'low', '100% cotton']
['mossimo', 'blue', 'bootcut', '11', None, '32', None, 'juniors', 'low rise', '100% cotton']
['lucky brand', 'blue', 'bootcut', '2', 'boot cut', '32', None, 'regular', 'low rise', 'cotton blend']
['j brand', 'blue', 'skinny & slim', '27 in.', None, '29', 'united states', 'regular', 'mid rise', 'cotton/polyester/elastane']
['big star', 'blue', None, '27 in.', None, '31', 'mexico', 'regular', 'low', 'denim']
['old navy', 'blue', None, '6', None, '27', 'china', 'regular', 'mid', 'cotton blend']
['7 for all mankind', 'blue', 'bootcut', '28 in.', 'boot cut', '34', 'united states', 'regular', 'high rise', 'cotton blend

['true religion', 'blue', None, '29 in.', None, '30', 'united states', 'regular', 'low', '100% cotton']
['gap', 'blue', 'straight', '29r', 'straight leg', '29', None, 'regular', 'mid', 'denim']
['miss me', 'blue', 'flare', '26', None, '31', None, 'regular', 'low', 'cotton blend']
['rock revival', 'blue', 'straight', '27 in.', 'straight leg', '32', 'china', 'regular', 'low', 'cotton blend']
['old navy', 'blue', None, '20', None, '31', None, 'regular', 'high', 'cotton blend']
['nydj', 'blue', None, '6', None, '32', None, 'regular', 'high', 'denim']
['lucky brand', 'blue', None, '4', None, '27', 'mexico', 'regular', 'mid', '100% cotton']
["levi's", 'blue', 'flare', '27 in.', 'flare', '32', None, 'regular', 'high', 'cotton blend']
['hudson', 'black', 'cargo', '27', None, '30', 'united states', 'regular', 'low', 'cotton']
["levi's", 'blue', 'bootcut', '12', None, '30', None, 'regular', 'low', 'cotton blend']
["levi's", 'blue', 'bootcut', '8 short', None, '30', None, 'petites', 'mid', 'cotto

['simply vera vera wang', 'blue', 'bootcut', '8', None, '31', 'cambodia', 'regular', 'mid', 'cotton blend']
["levi's", 'blue', 'skinny & slim', '24 in.', 'slim', '30', None, 'regular', 'mid-rise', 'cotton blend']
['paige', 'blue', 'bootcut', '25 in.', None, '31', None, 'regular', 'low', 'cotton blend']
['hudson', 'blue', 'bootcut', '27', None, '32', 'mexico', 'regular', 'low', 'cotton blend']
['madewell', 'green', 'skinny & slim', '25 in.', None, '26', None, 'regular', 'high', 'cotton/elastane']
['venezia', 'blue', 'cargo', '14', None, '30"', 'china', 'regular', 'mid', 'cotton blend']
["levi's", 'blue', 'straight', '7', None, '30"', 'mexico', 'regular', 'low', 'cotton']
['7 for all mankind', 'blue', 'bootcut', '24 in.', None, '31', 'united states', 'regular', 'low', 'cotton blend']
['old navy', 'blue', 'skinny & slim', '4', None, '30', 'cambodia', 'regular', 'mid', 'cotton/polyester/elastane']
['diesel', 'blue', 'boyfriend', '30 in.', None, '25', None, 'regular', 'low', 'cotton blend']

['seven for all mankind', None, None, '27 in.', 'boot cut', '27', 'mexico', 'regular', 'low', 'denim']
['old navy', 'black', None, '12', 'boot cut', '28.5', None, 'plus', 'low', 'denim']
['express', None, None, '8', 'flare', '34', None, 'regular', 'mid-rise', '75% cotton 24% polyester 1% soandex']
['diesel', 'blue', 'jeggings', '26 in.', 'slim', '30', 'united states', 'regular', 'low', 'denim']
['riders', 'blue', 'bootcut', '12m', None, '29', 'mexico', 'regular', 'mid rise', 'cotton blend']
['paige premium denim', 'blue', 'bootcut', '27 in.', 'boot cut', '31', 'united states', 'regular', 'low', 'denim']
['lee', 'blue', None, '6', 'boot cut', '31', 'indonesia', 'regular', 'mid-rise', 'cotton blend']
['madewell', 'blue', None, '26', 'slim', '32', 'china', 'regular', 'low', 'denim']
['j brand', 'blue', 'flare', '26', 'flare', '34', 'united states', 'regular', 'high', 'cotton']
['talbots', 'blue', 'bootcut', '8', None, '31', 'hong kong', 'regular', 'mid', '99% cotton 1% spandex']
['calvin 

['calvin klein', 'blue', 'straight', '26 in.', None, '31', 'united states', 'regular', 'high waist', '100% cotton']
["levi's", 'blue', 'tapered', '14', None, '30', 'mexico', 'regular', 'high', '100% cotton']
['diesel', 'blue', 'straight', '27 in.', None, '32', None, 'regular', 'mid', 'cotton blend']
['miss me', 'blue', None, '29 in.', None, '33', None, 'regular', 'low', 'denim']
['diesel', 'blue', 'boyfriend', '27 in.', None, '26', None, 'regular', 'low', 'cotton blend']
['diesel', 'black', 'jeggings', '27 in.', None, '34', None, 'regular', 'low', 'cotton blend']
['true religion', 'blue', 'straight', '27 in.', 'straight leg', '32', 'united states', 'regular', 'low', 'cotton blend']
['rock revival', 'blue', 'bootcut', '26 in.', None, '30', None, 'regular', 'low', '98% cotton']
['diesel', 'blue', 'jeggings', '29 in.', None, '34', None, 'regular', 'low', 'cotton blend']
['diesel', 'blue', 'skinny & slim', '30 in.', None, '30', None, 'regular', 'low', 'cotton blend']
['coldwater creek', 'b

In [181]:
#dataframe with attribute values
categories = pd.DataFrame(all_maps)
print(categories)

                                    0                                       1  \
0     old navy                         None                                     
1     american eagle outfitters        blue                                     
2     paige                            white                                    
3     old navy                         blue                                     
4     mossimo                          blue                                     
5     lucky brand                      blue                                     
6     j brand                          blue                                     
7     big star                         blue                                     
8     old navy                         blue                                     
9     7 for all mankind                blue                                     
10    j.crew                           blue                                     
11    miss me               

In [182]:
from sklearn.preprocessing import OneHotEncoder
x = OneHotEncoder().fit_transform(all_maps)
print(x)
print(type(x))

  (0, 196)	1.0
  (0, 381)	1.0
  (0, 480)	1.0
  (0, 576)	1.0
  (0, 1157)	1.0
  (0, 1260)	1.0
  (0, 1384)	1.0
  (0, 1385)	1.0
  (0, 1400)	1.0
  (0, 1691)	1.0
  (1, 13)	1.0
  (1, 284)	1.0
  (1, 480)	1.0
  (1, 819)	1.0
  (1, 1044)	1.0
  (1, 1268)	1.0
  (1, 1343)	1.0
  (1, 1389)	1.0
  (1, 1396)	1.0
  (1, 1644)	1.0
  (2, 198)	1.0
  (2, 378)	1.0
  (2, 480)	1.0
  (2, 712)	1.0
  (2, 1226)	1.0
  :	:
  (6999, 1316)	1.0
  (6999, 1379)	1.0
  (6999, 1389)	1.0
  (6999, 1399)	1.0
  (6999, 1644)	1.0
  (7000, 155)	1.0
  (7000, 284)	1.0
  (7000, 396)	1.0
  (7000, 819)	1.0
  (7000, 1230)	1.0
  (7000, 1290)	1.0
  (7000, 1364)	1.0
  (7000, 1389)	1.0
  (7000, 1398)	1.0
  (7000, 1671)	1.0
  (7001, 171)	1.0
  (7001, 284)	1.0
  (7001, 480)	1.0
  (7001, 540)	1.0
  (7001, 1104)	1.0
  (7001, 1299)	1.0
  (7001, 1364)	1.0
  (7001, 1389)	1.0
  (7001, 1400)	1.0
  (7001, 1691)	1.0
<class 'scipy.sparse.csr.csr_matrix'>


In [183]:
from sklearn.cluster import KMeans
kmeans = KMeans(n_clusters=5, random_state=0,verbose=True, n_init=2).fit(x)

Initialization complete
Iteration 0, inertia 71548.0
Iteration 1, inertia 43178.20292731956
Iteration 2, inertia 42575.80179000815
Iteration 3, inertia 42396.51780390255
Iteration 4, inertia 42172.6757806507
Iteration 5, inertia 41948.41140912857
Iteration 6, inertia 41850.28493110841
Iteration 7, inertia 41761.07928763553
Iteration 8, inertia 41534.63167953871
Iteration 9, inertia 41482.26260559074
Iteration 10, inertia 41479.63179001431
Iteration 11, inertia 41479.21146857988
Iteration 12, inertia 41479.11182304133
Converged at iteration 12: strict convergence.
Initialization complete
Iteration 0, inertia 75176.0
Iteration 1, inertia 43784.97264294723
Iteration 2, inertia 42543.00557858037
Iteration 3, inertia 42273.11015629992
Iteration 4, inertia 42016.68341411383
Iteration 5, inertia 41895.71150807186
Iteration 6, inertia 41812.69279592562
Iteration 7, inertia 41756.865335702416
Iteration 8, inertia 41681.64584890095
Iteration 9, inertia 41584.84426442678
Iteration 10, inertia 415

In [184]:
"""
Analysis of K-Means output
"""
count = {}
preds = []
actuals = []
for i, label in enumerate(kmeans.labels_):
    if label not in count:
        count[label] = 0
    count[label] += 1
#     print(f'row {i}\n: {df.iloc[i]}')
    ID = validation_rows.iloc[i]['index']
    if ID in valid.index:
        preds.append(label)
        actual = valid.loc[ID]['Group']
        actuals.append(actual)
#     print(f'ID: {ID}, pred: {label}, actual: {actual}')
print(count)
print(kmeans.inertia_)

evaluate(actuals, preds)

{4: 1205, 0: 1725, 3: 1480, 2: 956, 1: 1636}
41479.11182304133
Confusion Matrix:
[[38819484 10200796]
 [      38      684]]
precision: 6.70490948372197e-05
recall: 0.9473684210526315
f1 score: 0.00013408869967483492


In [249]:
from sklearn.cluster import AgglomerativeClustering

def cluster(data):
    clustering = AgglomerativeClustering(compute_distances=True,compute_full_tree = True,distance_threshold = 0.1,n_clusters=None).fit(data)
    print(clustering)
#     print("LABELS")
#     print(clustering.labels_)
#     print(len(clustering.labels_))
#     print(len(set(clustering.labels_)))
#     print("DISTAnCES")
#     print(clustering.distances_)
#     print("num connected components")
#     print(clustering.n_connected_components_)
    # make this better
    # make this work on the entire dataset
    # fix nonetypes
    # don't punish missing attributes, but punish conflicts. how do we encode this?

    return clustering

In [186]:
x = x.toarray() # only run this once

In [28]:
# x *= 10
x

array([[10.,  0.,  0., ...,  0.,  0., 10.],
       [10.,  0.,  0., ...,  0.,  0., 10.],
       [10.,  0.,  0., ...,  0.,  0., 10.],
       ...,
       [10.,  0.,  0., ...,  0.,  0., 10.],
       [10.,  0.,  0., ...,  0.,  0., 10.],
       [10.,  0.,  0., ...,  0.,  0., 10.]])

In [250]:
full_clustering = [0] * len(x)
count_so_far = 0
for label in count:
    print(f'now clustering group {label}')
    indices = [i for i in range(x.shape[0]) if kmeans.labels_[i] == label]
    data = [x[i] for i in indices]
    c = cluster(data)
    for i, label in enumerate(c.labels_):
        full_clustering[indices[i]] = label + count_so_far
#     print(c.labels_)
    count_so_far += len(data)

now clustering group 4
AgglomerativeClustering(compute_distances=True, compute_full_tree=True,
                        distance_threshold=0.0001, n_clusters=None)
now clustering group 0
AgglomerativeClustering(compute_distances=True, compute_full_tree=True,
                        distance_threshold=0.0001, n_clusters=None)
now clustering group 3
AgglomerativeClustering(compute_distances=True, compute_full_tree=True,
                        distance_threshold=0.0001, n_clusters=None)
now clustering group 2
AgglomerativeClustering(compute_distances=True, compute_full_tree=True,
                        distance_threshold=0.0001, n_clusters=None)
now clustering group 1
AgglomerativeClustering(compute_distances=True, compute_full_tree=True,
                        distance_threshold=0.0001, n_clusters=None)


In [30]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', -1)

<ipython-input-30-1390d13c0cdd>:4: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('display.max_colwidth', -1)


In [251]:
groups = {}
for i, label in enumerate(full_clustering):
    if label not in groups:
        groups[label] = []
    groups[label].append(i)
groups = {label: groups[label] for label in groups if len(groups[label]) > 1}
print(groups)
for label in groups:
    print(f'GROUP: {label}')
    for item in groups[label]:
        print(validation_rows['Tags'].iloc[[item]].to_string())
    print('-----------------')


{5420: [16, 5256], 2973: [17, 5397], 1324: [24, 4815], 5421: [28, 3542], 1331: [60, 888], 1206: [73, 3111, 6190], 2983: [76, 1646, 6056], 1229: [79, 1035, 2520, 4276, 4638, 4639, 4999, 5310, 6757], 53: [82, 3685], 1264: [133, 134, 3253], 1237: [138, 1148, 2629, 3336, 5472], 5374: [139, 3759], 2980: [152, 5653], 3221: [163, 1034], 2957: [176, 5991], 1269: [185, 5458], 2959: [188, 195, 995, 1037, 1655, 2399, 2464, 3191, 3223, 3544, 3819, 4551, 5441, 5803, 6186, 6952], 1394: [190, 240], 3006: [191, 606, 4549, 5321], 1288: [200, 237, 3955, 4636], 1234: [202, 2479], 5390: [225, 226], 2974: [228, 233, 2511], 5395: [231, 3891], 1334: [239, 248, 1652, 4672], 2986: [242, 600], 1330: [243, 607], 1251: [245, 900, 1644, 2110, 3098, 3112, 4546, 5587, 6185], 5370: [257, 5495], 5388: [268, 3126], 1278: [279, 4062], 5379: [314, 4022], 2987: [358, 359], 2940: [362, 5529], 5383: [375, 5561], 2941: [377, 2595], 1242: [405, 4098], 1472: [408, 4099], 3005: [412, 489], 1218: [418, 6342], 2935: [440, 1939], 

306696    (Model:Hudson Signature Bootcut,Features:Stretch,Country/Region of Manufacture:United States,Inseam:31,Rise:Low,Length:Full Length,Material:Cotton Blend,Wash:Dark,Treatment:Dark Wash,Distressed,Style:Boot Cut,Size Type:Regular,Color:Blue,Bottoms Size (Women's):27 in.,Silhouette:Bootcut,Modified Item:Yes,Brand:HUDSON,Modification Description:Hem up)
853844    (Actual Waist Measurement:30 inches (Aligned at top),Inseam:31,Material:Cotton Blend,Length:Full Length,Treatment:Dark Wash,Style:Boot Cut,Size Type:Regular,Silhouette:Bootcut,Rise:Low,Modified Item:Yes,Wash:Dark Blue,Modification Description:Hem up and waist taken in,Model:Hudson Signature Bootcut,Important:See "Measurements"-click Blue "Read More" link below Item Des,Features:Stretch,Country/Region of Manufacture:United States,Color:Blue,Brand:HUDSON,Bottoms Size (Women's):27 in.)
959453    (Inseam:31,Brand:HUDSON,Bottoms Size (Women's):27 in.,Length:Full Length,Wash:Slightly Darker Blue with distressing,Treatment:Distr

In [252]:
print(len(groups))

253


In [253]:
"""
Evaluate clustering after it has gone through k-means and agglomorative clustering.
"""
p = full_clustering
print(full_clustering)
actuals = []
for i in range(len(p)):
    ID = validation_rows.iloc[i]['index']
    if ID in valid.index:
        actual = valid.loc[ID]['Group']
        actuals.append(actual)
a = actuals # valid['Group'].tolist()
print(len(set(p)))
print(len(p))
evaluate(a, p)

[1087, 2112, 869, 2804, 4046, 5162, 6964, 2532, 6791, 5161, 6501, 4304, 5329, 607, 2531, 2530, 5420, 2973, 4935, 842, 841, 4946, 2529, 5098, 1324, 6181, 6785, 2802, 5421, 2432, 6960, 2749, 5120, 4303, 1058, 2752, 3723, 5115, 2204, 2737, 6959, 2786, 6784, 6783, 2104, 6782, 840, 1056, 1167, 2103, 6957, 5268, 1158, 2461, 2492, 1053, 4907, 3838, 4926, 5222, 1331, 641, 6597, 6765, 812, 2460, 6764, 6790, 2459, 2488, 2102, 2454, 2480, 1206, 2736, 5133, 2983, 2524, 6492, 1229, 2750, 602, 53, 865, 1131, 4299, 6598, 3722, 2453, 2455, 808, 3783, 6939, 4038, 2193, 6755, 5064, 1083, 4963, 4938, 5156, 2505, 2745, 2730, 6559, 6557, 3971, 3716, 6177, 2744, 800, 4039, 1057, 1165, 5313, 4196, 6500, 3991, 6472, 2101, 4026, 881, 2790, 2449, 6789, 5264, 639, 6179, 2486, 5322, 2462, 4195, 6768, 1264, 1264, 6709, 6231, 6465, 1237, 5374, 2479, 829, 3715, 6423, 2528, 6273, 5210, 5099, 6825, 2527, 5052, 5199, 2980, 2723, 3714, 5306, 6655, 3769, 6371, 4905, 6747, 2789, 6779, 3221, 6356, 1054, 5160, 6761, 4934, 2

6670
7002
Confusion Matrix:
[[49019698      582]
 [     152      570]]
precision: 0.4947916666666667
recall: 0.7894736842105263
f1 score: 0.6083244397011739


In [220]:
"""
Functions used to display the tags in a nicer manner below.
"""
def get_mapping(attribute):
    attribute = re.sub(r'[()]','', attribute)
#     attribute = re.split(r',', attribute)
#     attribute = [a.split(':') for a in attribute]
    attribute = re.split(r':+', attribute)
    attribute = [a.split(',') for a in attribute]
    '''
    for i, a in enumerate(attribute):
        attribute[i] = [s.strip() for s in a]
        all_attributes.add(attribute[i][0])
    #print(f'atttribute is: {attribute}')
    '''
    mapping = {}
    for i in range(len(attribute) - 1):
        if i == len(attribute) - 2:
            mapping[attribute[i][-1]] = attribute[i + 1][:]
        else:
            mapping[attribute[i][-1]] = attribute[i + 1][:-1]
    return mapping

def mapping_to_string(mapping):
    keys = list(mapping.keys())
    keys.sort()
    return ';'.join([f'{key}:{list(sorted(mapping[key]))}' for key in keys])

In [221]:
"""
Show the items where the two clusterings ,p(redict) and a(ctual), differ.
"""
for i in range(len(a)):
    for j in range(len(p)):
        if i != j:
            if a[i] == a[j] and p[i] != p[j]:
                print("These two items should be in the same group:")
            elif a[i] != a[j] and p[i] == p[j]:
                continue
                print("These two items should not be in the same group")
            else:
                continue
            print(f"tags: {mapping_to_string(get_mapping(validation_rows['Tags'].iloc[[i]].to_string(index=False)))}")
            print(f"urls: {validation_rows['primary_image_url'].iloc[[i]].to_string()}")
            print(f"tags: {mapping_to_string(get_mapping(validation_rows['Tags'].iloc[[j]].to_string(index=False)))}")
            print(f"urls: {validation_rows['primary_image_url'].iloc[[j]].to_string()}")
            print('-------------------')

These two items should be in the same group:
tags: Bottoms Size Women's:['8'];Brand:['Lucky Brand'];Color:['Blue'];Country/Region of Manufacture:['China'];Garment Care:['Machine Washable'];Inseam:['31'];Length:['Full Length'];Material:['Cotton Blend'];Pattern:['Solid'];Rise:['Mid'];Silhouette:['Bootcut'];Size Type:['Regular'];Treatment:['Dark Wash', 'Medium Wash', 'Stone Wash']
urls: 54801    https://i.ebayimg.com/00/s/MTU2OVg5ODk=/z/OUAAAOSwtbdc6pWq/$_57.JPG?set_id=8800005007
tags: Bottoms Size Women's:['8'];Brand:['Lucky Brand'];Color:['Blue'];Country/Region of Manufacture:['China'];Inseam:['31'];Length:['Full Length'];Material:[' 1% Spandex', '99% Cotton'];Rise:['Mid Rise'];Size Type:['Regular'];Style:['Boot'];Treatment:['Dark Wash'];Wash:['Dark']
urls: 444298    https://i.ebayimg.com/00/s/NTQxWDUyMw==/z/u4gAAOSwR6Bb2HkU/$_57.JPG?set_id=8800005007
-------------------
These two items should be in the same group:
tags: Accents:['Embellished'];Bottoms Size Women's:['00'];Brand:['Miss M

These two items should be in the same group:
tags: Bottoms Size Women's:['31 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['25'];Length:['Crop'];Material:['Cotton Blend'];Model:['Diesel Fayza'];Pattern:['Solid'];Rise:['Low'];Silhouette:['Boyfriend', 'Relaxed'];Size Type:['Regular'];Treatment:['Dark Wash', 'Distressed', 'Faded']
urls: 91826    https://i.ebayimg.com/00/s/NTgwWDU4MA==/z/rKsAAOSwBdJc7~FA/$_57.JPG?set_id=8800005007
tags: Bottoms Size Women's:['30 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['25'];Length:['Crop'];Material:['Cotton Blend'];Model:['Fayza Relaxed-Boyfriend'];Modified Item:['No'];Pattern:['Solid'];Rise:['Low'];Silhouette:['Boyfriend', 'Relaxed'];Size Type:['Regular'];Treatment:['Dark Wash', 'Distressed']
urls: 577618    https://i.ebayimg.com/00/s/NDk2WDUwMA==/z/7G0AAOSwoQdc8VN4/$_57.PNG?set_id=8800005007
-------------------
These two items should be in 

These two items should be in the same group:
tags: Bottoms Size Women's:['27 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['32'];Length:['Crop'];Material:['Cotton Blend'];Model:['Diesel Fayza'];Modified Item:['No'];Pattern:['Solid'];Rise:['Low'];Silhouette:['Boyfriend', 'Relaxed'];Size Type:['Regular'];Treatment:['Dark Wash', 'Distressed']
urls: 207898    https://i.ebayimg.com/00/s/NTc0WDU3OQ==/z/GHMAAOSwailc7W3C/$_57.PNG?set_id=8800005007
tags: Bottoms Size Women's:['27in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['32'];Length:['Crop'];Material:['Cotton Blend'];Model:['Diesel Fayza'];Pattern:['Solid'];Rise:['Low'];Silhouette:['Boyfriend', 'Relaxed'];Size Type:['Regular'];Treatment:['Dark Wash', 'Distressed', 'Faded']
urls: 91734    https://i.ebayimg.com/00/s/NTgwWDU4MA==/z/rKsAAOSwBdJc7~FA/$_57.JPG?set_id=8800005007
-------------------
These two items should be in the same gro

These two items should be in the same group:
tags: Bottoms Size Women's:['25'];Brand:['Banana Republic'];Color:['Black'];Inseam:['28'];Material:[' 3% spandex.', ' 6% polyester', '91% cotton'];Pattern:['Solid'];Rise:['Mid-Rise'];Size Type:['Regular'];Style:[' Skinny', 'Slim'];Wash:['Black & Gray']
urls: 255419    https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/95IAAOSwWOxbOV6o/$_57.JPG?set_id=8800005007
tags: Bottoms Size Women's:['25'];Brand:['Banana Republic'];Color:['Black'];Inseam:['28'];Material:[' 3% spandex.', ' 6% polyester', '91% cotton'];Modified Item:['No'];Pattern:['Solid'];Rise:['Mid Rise'];Size Type:['Regular'];Style:['Skinny']
urls: 74889    https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/wOAAAOSwMbRbZLSY/$_57.JPG?set_id=8800005007
-------------------
These two items should be in the same group:
tags: Bottoms Size Women's:['28 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['34'];Length:['Full Length'];Material:['Cotton Blend'];Mod

These two items should be in the same group:
tags: Bottoms Size Women's:['26 in.'];Brand:['J.CREW'];Color:['White'];Inseam:['25'];Length:['Ankle'];Material:['100% Cotton'];Modified Item:['No'];Rise:['Mid-Rise'];Size Type:['Regular'];Style:[' Skinny', 'Slim'];Treatment:['White'];Wash:['White']
urls: 291287    https://i.ebayimg.com/00/s/MTYwMFgxNjAw/z/RVMAAOSwj3xbP6Yr/$_12.JPG?set_id=880000500F
tags: Bottoms Size Women's:['26 in.'];Brand:['J.CREW'];Inseam:['25'];Material:['100% Cotton'];Rise:['Mid-Rise'];Size Type:['Regular'];Style:[' Skinny', 'Slim'];Wash:['White']
urls: 215451    https://i.ebayimg.com/00/s/NzQ5WDk5OQ==/z/mwcAAOSwfbpbnDh-/$_12.JPG?set_id=880000500F
-------------------
These two items should be in the same group:
tags: Bottoms Size Women's:['28 in.'];Brand:['7 For All Mankind'];Color:['Blue'];Features:['Stretch'];Inseam:['31'];Length:['Full Length'];Material:['Cotton Blend'];Model:['7 for all Mankind Bootcut'];Modification Description:['Hem up'];Modified Item:['Yes'];Ris

...

These two items should be in the same group:
tags: Bottoms Size Women's:['12'];Brand:['OLD NAVY'];Features:['Stretch', 'Zipper Closure'];Inseam:['31 INCHES'];Length:['Full Length'];Material:['Cotton Spandex'];Rise:['Mid-Rise'];Silhouette:['Straight'];Size Type:['Regular'];Style:['Boot Cut', 'SLIM STRAIGHT'];Treatment:['Distressed'];UPC:['Does Not Apply'];Wash:['Distressed']
urls: 710703    https://i.ebayimg.com/00/s/MTIwMFg5MDA=/z/wEgAAOSwpKxdIot4/$_12.JPG?set_id=880000500F
tags: Bottoms Size Women's:['12'];Brand:['OLD NAVY'];Inseam:['31 INCHES'];Length:['Full Length'];Material:['Cotton Spandex'];Rise:['Mid-Rise'];Size Type:['Regular'];Style:['Boot Cut', 'SLIM STRAIGHT'];UPC:['Does Not Apply'];Wash:['Distressed']
urls: 226225    https://i.ebayimg.com/00/s/MTIwMFg5MDA=/z/MAcAAOSw1AVcpEF9/$_12.JPG?set_id=880000500F
-------------------
These two items should be in the same group:
tags: Bottoms Size Women's:['26 in.'];Brand:['BIG STAR'];Color:['Blue'];Features:['Stretch'];Inseam:['32'];Len

These two items should be in the same group:
tags: Bottoms Size Women's:['28 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['30'];Length:['Full Length'];Material:['Cotton Blend'];Model:['Diesel Straitzee'];Modified Item:['No'];Pattern:['Solid'];Rise:['Mid'];Silhouette:['Slim', 'Straight'];Size Type:['Regular'];Treatment:['Dark Wash', 'Raw Denim']
urls: 759004    https://i.ebayimg.com/00/s/NjUwWDQzNA==/z/AW0AAOSwJh1dAUqk/$_57.JPG?set_id=8800005007
tags: Bottoms Size Women's:['28 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch', 'Zipper Closure'];Garment Care:['Machine Washable'];Inseam:['30'];Length:['Full Length'];Material:['Cotton Blend'];Model:['Diesel Straitzee'];Modified Item:['No'];Pattern:['Solid'];Rise:['Mid'];Silhouette:['Straight'];Size Type:['Regular'];Treatment:['Dark Wash']
urls: 233140    https://i.ebayimg.com/00/s/NjUwWDQzNA==/z/IvUAAOSwoqNc8A8P/$_57.JPG?set_id=8800005007
-------------------
These two items sh

These two items should be in the same group:
tags: Bottoms Size Women's:['24 in.'];Brand:['Mih'];Color:['Black'];Country/Region of Manufacture:['Turkey'];Features:['Can Roll Up'];Garment Care:['Machine Washable'];Inseam:['30'];Length:['Full Length'];Material:['Cotton Blend'];Model:['Phoebe'];Pattern:['Solid'];Rise:['High'];Size Type:['Regular'];Wash:['Black']
urls: 813603    https://i.ebayimg.com/00/s/MTU3M1g4Mjk=/z/tMIAAOSwTEZcFyyt/$_12.JPG?set_id=880000500F
tags: Bottoms Size Women's:['24 in.'];Brand:['Mih'];Color:['Black'];Country/Region of Manufacture:['Turkey'];Features:['Can Roll Up'];Garment Care:['Machine Washable'];Inseam:['30'];Length:['Full Length'];Material:['Cotton Blend'];Model:['Phoebe'];Pattern:['Solid'];Rise:['High'];Silhouette:['Boyfriend'];Size Type:['Regular'];Style:['Phoebe'];Wash:['Black']
urls: 579123    https://i.ebayimg.com/00/s/MTU3M1g4Mjk=/z/tMIAAOSwTEZcFyyt/$_12.JPG?set_id=880000500F
-------------------
These two items should be in the same group:
tags: Bott

These two items should be in the same group:
tags: Bottoms Size Women's:['27 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['32'];Length:['Crop'];Material:['Cotton Blend'];Model:['Diesel Fayza'];Modified Item:['No'];Pattern:['Solid'];Rise:['Low'];Silhouette:['Boyfriend', 'Relaxed'];Size Type:['Regular'];Treatment:['Dark Wash', 'Distressed']
urls: 888423    https://i.ebayimg.com/00/s/NDk2WDUwMA==/z/7G0AAOSwoQdc8VN4/$_57.PNG?set_id=8800005007
tags: Bottoms Size Women's:['27in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['32'];Length:['Crop'];Material:['Cotton Blend'];Model:['Diesel Fayza'];Pattern:['Solid'];Rise:['Low'];Silhouette:['Boyfriend', 'Relaxed'];Size Type:['Regular'];Treatment:['Dark Wash', 'Distressed', 'Faded']
urls: 91734    https://i.ebayimg.com/00/s/NTgwWDU4MA==/z/rKsAAOSwBdJc7~FA/$_57.JPG?set_id=8800005007
-------------------
These two items should be in the same gro

These two items should be in the same group:
tags: Bottoms Size Women's:['25 in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['32'];Length:['Full Length'];Material:['Cotton Blend'];Model:['Diesel Skinzee'];Modified Item:['No'];Pattern:['Solid'];Rise:['Mid'];Silhouette:['Skinny & Slim'];Size Type:['Regular'];Treatment:['Dark Wash']
urls: 975333    https://i.ebayimg.com/00/s/MTYwMFgxMjAw/z/hL0AAOSw6pxdCPfj/$_57.JPG?set_id=8800005007
tags: Bottoms Size Women's:['25in.'];Brand:['Diesel'];Color:['Blue'];Features:['Stretch'];Garment Care:['Machine Washable'];Inseam:['32'];Length:['Full'];Material:['Cotton Blend'];Model:['Diesel Skinzee'];Modified Item:['No'];Pattern:['Solid'];Rise:['Mid'];Silhouette:['Skinny & Slim'];Size Type:['Regular'];Treatment:['Dark Wash', 'Raw Denim']
urls: 580605    https://i.ebayimg.com/00/s/ODUzWDY0MA==/z/ORsAAOSwqYxdApv~/$_57.JPG?set_id=8800005007
-------------------
These two items should be in the same group:
t

In [27]:
old_clustering = full_clustering
print(old_clustering)

[1491, 1690, 175, 70, 12, 2712, 2514, 250, 1392, 140, 885, 1656, 2822, 1655, 2820, 253, 2689, 1380, 884, 1650, 342, 1423, 1639, 934, 1633, 909, 52, 52, 915, 2764, 1674, 1390, 985, 391, 1421, 2756, 2823, 2832, 2513, 1619, 2172, 1345, 1335, 2818, 2140, 20, 77, 2746, 2511, 1342, 929, 1145, 2, 82, 1057, 72, 535, 2512, 1129, 2123, 875, 2757, 54, 874, 85, 1368, 2849, 295, 2783, 176, 402, 1642, 2759, 949, 1651, 1495, 2843, 61, 2139, 2115, 591, 940, 1535, 1, 945, 2114, 2658, 1686, 43, 1693, 1692, 1264, 2791, 1117, 1386, 3, 1541, 1667, 1349, 1638, 2108, 1020, 1475, 2704, 2178, 2116, 1594, 1389, 1379, 1231, 3, 1137, 372, 2129, 2133, 1585, 1084, 1131, 36, 2636, 1478, 1565, 2509, 268, 279, 2816, 1062, 1253, 7, 342, 1155, 1076, 708, 1042, 1306, 159, 1130, 23, 1432, 2157, 116, 2634, 1258, 2733, 2807, 1348, 867, 1039, 1387, 1102, 1682, 2770, 2889, 160, 126, 2109, 2, 1632, 1493, 2588, 1225, 1081, 1399, 1680, 1294, 138, 1238, 1189, 2706, 1331, 1292, 694, 1677, 1321, 20, 71, 1016, 2799, 2653, 2709, 498,

In [ ]:
%matplotlib qt
import matplotlib.pyplot as plt
from scipy.cluster.hierarchy import dendrogram
import numpy as np
from PIL import Image
import requests
from io import BytesIO

def plot_dendrogram(model, **kwargs):
    counts = np.zeros(model.children_.shape[0])
    n_samples = len(model.labels_)
    for i, merge in enumerate(model.children_):
        current_count = 0
        for child_idx in merge:
            if child_idx < n_samples:
                current_count += 1  # leaf node
            else:
                current_count += counts[child_idx - n_samples]
        counts[i] = current_count

    linkage_matrix = np.column_stack([model.children_, model.distances_,
                                      counts]).astype(float)

    #response = requests.get(url)
    #img = Image.open(BytesIO(response.content))
    link_labels = [df['Tags'][i] for i in clustering.labels_]
    dendrogram(linkage_matrix, labels = link_labels)
plot_dendrogram(clustering)
plt.show()

In [ ]:
# Simple parsing logic for attributes - works well
import re
from collections import Counter
freq=Counter()
attribute=[['']]*len(df)
trialrange=500
for x in range(trialrange):#range(int(len(df)/10)):#len(df)
    attribute[x]=df.iloc[x,3].lower()
    attribute[x] = re.sub(r'[()]','', attribute[x])
    attribute[x] = re.split(r',', attribute[x])
    attribute[x] = [a.split(':') for a in attribute[x]]
    freq+=Counter([i[0] for i in attribute[x]])
    tempdict={}
    for i in attribute[x]:

            try:
                tempdict[i[0]]=float(i[1])
            except:
                try:
                    tempdict[i[0]]=i[1]
                except:
                    pass
    attribute[x]=tempdict

df['seg']=attribute
#print(df['seg'])

In [ ]:
Brands=[]
Images=[]
print(trialrange)
for i in range(trialrange):
    try:
        #df['seg'].iloc[i]['brand']
        #df['primary_image_url'].iloc[i]
        #print(df['seg'].iloc[i]['brand'])
        #print(df['primary_image_url'].iloc[i])
        Brands.append(df['seg'].iloc[i]['brand'])
        Images.append(df['primary_image_url'].iloc[i])
    except:
        Brands.append('None')
        print('not possible at: ',i)

In [ ]:
n = 500
from PIL import Image, ImageFile
import requests
from io import BytesIO
import numpy as np
ImageFile.LOAD_TRUNCATED_IMAGES = True

'''
url = df['primary_image_url'][4]
response = requests.get(url)
#img = Image.open(BytesIO(response.content))
img = Image.open(requests.get(url, stream=True).raw)
img.show()
result = Image.new(img.mode, (1000, 550), (64,64,64))
result.paste(img, (0, 0))
result.show()
print(np.asarray(img).shape)
print(np.asarray(result).shape)
'''
image_array = []
images = []
max_height = 0
max_width = 0
i = 0
for img in df['primary_image_url'][0:n]:
    response = requests.get(img)
    if i%20 == 0:
        print(i)
    i+=1
    img = Image.open(BytesIO(response.content))
    if np.asarray(img).shape[1] > max_width:
        max_width = np.asarray(img).shape[1]
    if np.asarray(img).shape[0] > max_height:
        max_height = np.asarray(img).shape[0]
    images.append(img)
i=0
for img in images:
    if i%20 == 0:
        print(i)
    i+=1
    try:
        img = img.convert('RGB')
        margin = Image.new(img.mode, (max_width, max_height), (64,64,64))
    except:
        img = img.convert('RGB')
        margin = Image.new(img.mode,(max_width,max_height),(64,64,64))
    margin.paste(img, (0, 0))
    image_array.append(np.asarray(margin))

In [ ]:

#import sys
#print(sys.version)
#%pip install tensorflow

import tensorflow as tf
from tensorflow.keras import datasets, layers, models
model = models.Sequential()
model.add(layers.Conv2D(1, (3, 3), activation='relu', input_shape=(max_width, max_height, 3)))
model.add(layers.MaxPooling2D((2, 2)))
model.add(layers.Flatten())
#model.add(layers.Dense(4, activation='relu'))
model.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

In [ ]:
brand_dict = {}
num = 0
labels = []
for b in Brands:
    if b not in brand_dict:
        brand_dict[b] = num
        num+=1
    labels.append(brand_dict[b])

m = 500
n = round(m*.8)
train_images = np.asarray(image_array[0:n])
test_images = np.asarray(image_array[n:])
train_labels = np.asarray(labels[0:n])
test_labels = np.asarray(labels[n:])
print(type(test_images[0]))

In [ ]:
history = model.fit(train_images, train_labels, epochs=5, 
                    validation_data=(test_images, test_labels))